### LIBRARY IMPORT

In [74]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)
from contextlib import contextmanager
import time  
from sklearn.neighbors import NearestNeighbors  
from sklearn.preprocessing import minmax_scale  
from typing import Dict, List, Optional, Tuple  
import seaborn as sns 
import gc
import traceback 

import matplotlib.pyplot as plt

from scipy.stats import kendalltau

import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()



180

### Drop Early morning period & CHECK NULL VALUE

In [80]:
# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
combined_result_df_raw = pd.read_csv("./output/BTC_sum_both_10m.csv")
print("# of rows of combined_Result_Df:", combined_result_df_raw.shape[0])

combined_result_df_raw['window_start'] = pd.to_datetime(combined_result_df_raw['window_start'])  # Convert to datetime

# Define the time range
start_time = pd.to_datetime('00:00:00').time()
end_time = pd.to_datetime('06:00:00').time()

# 10분간 return 추가
combined_result_df_raw['return'] = np.log(combined_result_df_raw['end_price'].shift(-10) / combined_result_df_raw['end_price'])

# Filter and drop rows (새벽시간 삭제하기)
filtered_df = combined_result_df_raw[~combined_result_df_raw['window_start'].apply(lambda x: start_time <= x.time() <= end_time)]
print("# of rows of filtered_df:", filtered_df.shape[0])

# Set the target variable:
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
print("target_var_3:", target_var_3)

# 사용하지 않을 변수(column)들 미리 제거 (dropna 효과를 최소화하기 위해.)
remove_varlist0 = [
                  'window_start', 
                  'window_end',
                  'prices_30s_for_NN',
                  'window_end_150_ticker',
                  'window_end_300_ticker',
                  'window_end_450_ticker',
                  'window_end_150_orderbook',
                  'window_end_300_orderbook',
                  'window_end_450_orderbook',

                  # 'volume_power',
                  # 'volume_power_150',
                  # 'volume_power_300',
                  # 'volume_power_450',
                  
                  'end_price',
                  'realized_volatility_30s',

                #   'dv1_realized_volatility',
                  'dv2_lowest_return',
                  'dv3_highest_return',
                  'dv4_realized_volatility_30s',
                  'dv5_realized_volatility_mean0',

                  # 'prices_30s_for_NN_onlyprices',
                  ]
remove_varlist0.remove(target_var)

# 이 두 아래의 변수도 NN feature를 뽑을 때에는 활용해보자.
remove_varlist0.remove('dv2_lowest_return')
remove_varlist0.remove('dv3_highest_return')

main_feature_list = list(filtered_df.columns)

for i in range(len(remove_varlist0)):
    # print(remove_varlist0[i])
    main_feature_list.remove(remove_varlist0[i])

## 제거하기 전에, 30초 주가 데이터를 따로 저장.
# listed_time_series_df = filtered_df['only_prices_30s_for_NN'].copy()
# combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)

filtered_df = filtered_df[main_feature_list]

combined_result_df = filtered_df.dropna()
print("# of rows of filtered_df:", combined_result_df.shape[0])

# 평균이 아닌 이전 값으로 Null 채우기
# combined_result_df = combined_result_df.fillna(method='ffill') 

# # Temporary take the first N rows
# take_first_rows = 30000
# combined_result_df = combined_result_df.head(take_first_rows)

# 오히려 초반 10000개를 떼어내고 분석하면?
# combined_result_df = combined_result_df.iloc[7000:]

print("combined_result_df.dtypes:", combined_result_df.dtypes)
print("combined_result_df.shape:", combined_result_df.shape)
combined_result_df.head(3)

gc.collect()

# of rows of combined_Result_Df: 102336
# of rows of filtered_df: 76766
target_var_3: dv5
# of rows of filtered_df: 76696
combined_result_df.dtypes: realized_volatility_mean0    float64
num_trades                     int64
lowest_return                float64
highest_return               float64
high_low_gap                 float64
                              ...   
tvpl_ep2                     float64
tvpl_ep5                     float64
tvpl_ep10                    float64
tvpl_ep15                    float64
return                       float64
Length: 96, dtype: object
combined_result_df.shape: (76696, 96)


0

In [81]:
import re
def extract_floats_from_series(df):
    def extract_floats(s):
        return [float(num) for num in re.findall(r"(-?\d+\.\d+)", s)]

    df['only_prices_30s_for_NN'] = df['prices_30s_for_NN_onlyprices'].apply(extract_floats)
    
    # 데이터 포인트가 20개가 아닌 행을 삭제
    mask = df['only_prices_30s_for_NN'].apply(len) == 20
    df = df[mask].reset_index(drop=True)
    
    return df

In [82]:
combined_result_df.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
38                   0.000105         376      -0.000089        0.001815   
39                   0.000107         361      -0.000089        0.001815   
40                   0.000106         365       0.000000        0.001815   

    high_low_gap  trade_vol  volume_power              time_id  BB_width_w20  \
38      0.001904  13.756273      1.442885  2022-12-16 21:44:00  48144.956559   
39      0.001904  12.615168      1.262884  2022-12-16 21:45:00  50564.809898   
40      0.001815  13.313910      1.278754  2022-12-16 21:46:00  53873.536126   

    BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
38  47257.071103  55194.202594                       0.000154   
39  50311.440306  54273.382058                       0.000156   
40  53013.302636  51861.353627                       0.000159   

    dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
38          -0.000310            0.001238                       0.000046   
39          -0.000177            0.001371                       0.000077   
40          -0.000044            0.001238                       0.000140   

    num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
38              85          -0.000089            0.000089          0.000177   
39              68          -0.000089            0.000354          0.000443   
40              69           0.000000            0.000354          0.000354   

    trade_vol_150  volume_power_150  realized_volatility_mean0_300  \
38       3.814411          1.452098                       0.000100   
39       1.921894          4.441761                       0.000106   
40       2.159312          2.504304                       0.000109   

    num_trades_300  lowest_return_300  highest_return_300  high_low_gap_300  \
38             147          -0.000089            0.000354          0.000443   
39             126          -0.000089            0.000399          0.000487   
40             125           0.000000            0.000753          0.000753   

    trade_vol_300  volume_power_300  realized_volatility_mean0_450  \
38       5.543539          1.719981                       0.000092   
39       3.760741          3.587342                       0.000116   
40       4.498119          5.960898                       0.000119   

    num_trades_450  lowest_return_450  highest_return_450  high_low_gap_450  \
38             209          -0.000089            0.001284          0.001373   
39             259          -0.000089            0.001815          0.001904   
40             286           0.000000            0.001815          0.001815   

    trade_vol_450  volume_power_450  liq_last_1  liq_last_2  liq_last_5  \
38       9.178568          3.329562    0.003128    0.003207    0.003479   
39       9.098996          2.272833    0.001286    0.001625    0.002044   
40       9.661851          1.848649    0.001621    0.001628    0.002304   

    liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  ep_liq_5  ep_liq_10  \
38     0.003642     0.003871  0.000475  0.000668  0.001029   0.001296   
39     0.002316     0.002420  0.000472  0.000647  0.000948   0.001205   
40     0.002582     0.002729  0.000489  0.000659  0.000952   0.001197   

    ep_liq_15  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
38   0.001752         2.030769        10.261539        0.001555   
39   0.001527         2.098361        13.000000        0.000299   
40   0.001454         1.487500         9.412500        0.000284   

    liq_last_2_150  liq_last_5_150  liq_last_10_150  liq_last_15_150  \
38        0.001703        0.002171         0.002716         0.003101   
39        0.000458        0.000700         0.001334         0.001723   
40        0.001064        0.001406         0.001930         0.002127   

    ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  ep_liq_15_150  \
38      0.001283      0.001609      0.002627       0.002997       0.0

In [83]:
combined_result_df = extract_floats_from_series(combined_result_df)
combined_result_df.reset_index(drop=True, inplace=True)
print("combined_result_df.shape (After dropping windows without 20 prices):", combined_result_df.shape)
listed_time_series_df = combined_result_df['only_prices_30s_for_NN'].copy()
combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)
combined_result_df = combined_result_df.drop('only_prices_30s_for_NN', axis=1)

gc.collect()

combined_result_df.shape (After dropping windows without 20 prices): (75030, 97)


c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


0

In [84]:
float64_features = combined_result_df.select_dtypes(include=['float64']).columns.tolist()
int64_features = combined_result_df.select_dtypes(include=['int64']).columns.tolist()

combined_result_df[float64_features] = combined_result_df[float64_features].astype('float32')
combined_result_df[int64_features] = combined_result_df[int64_features].astype('int32')

gc.collect()

0

In [85]:
print("combined_result_df.dtypes:", combined_result_df.dtypes)

combined_result_df.dtypes: realized_volatility_mean0    float32
num_trades                     int32
lowest_return                float32
highest_return               float32
high_low_gap                 float32
                              ...   
tvpl_ep2                     float32
tvpl_ep5                     float32
tvpl_ep10                    float32
tvpl_ep15                    float32
return                       float32
Length: 95, dtype: object


### Manipulating Features => Log transformation of some liquidity measures (Why?)

In [86]:
# combined_result_df['liq_last_1'] = np.log10(combined_result_df['liq_last_1'] + 0.00001)
# combined_result_df['liq_last_2'] = np.log10(combined_result_df['liq_last_2'] + 0.00001)
# combined_result_df['liq_last_5'] = np.log10(combined_result_df['liq_last_5'] + 0.00001)
# combined_result_df['liq_last_10'] = np.log10(combined_result_df['liq_last_10'] + 0.00001)
# combined_result_df['liq_last_15'] = np.log10(combined_result_df['liq_last_15'] + 0.00001)
# combined_result_df['trade_vol'] = np.log10(combined_result_df['trade_vol'] + 0.00001)
# combined_result_df['num_trades'] = np.log10(combined_result_df['num_trades'] + 0.00001)

### NUMERIC FEATURES & CALCULATE CORR 

In [87]:
## 이웃을 찾는 기준이 되는 변수들.

feature_list_for_finding_NN = []
feature_list_for_finding_NN.append('realized_volatility_mean0')
feature_list_for_finding_NN.append('bidask_spread_0')
feature_list_for_finding_NN.append('bidask_spread_1')
feature_list_for_finding_NN.append('highest_return')
feature_list_for_finding_NN.append('lowest_return')
feature_list_for_finding_NN.append('num_trades')
feature_list_for_finding_NN.append('high_low_gap')
feature_list_for_finding_NN.append('BB_width_w10')
feature_list_for_finding_NN.append('BB_width_w20')
feature_list_for_finding_NN.append('BB_width_w40')
feature_list_for_finding_NN.append('liq_last_1')
feature_list_for_finding_NN.append('liq_last_2')
feature_list_for_finding_NN.append('liq_last_5')
feature_list_for_finding_NN.append('ep_liq_1')
feature_list_for_finding_NN.append('ep_liq_2')
feature_list_for_finding_NN.append('ep_liq_5')
feature_list_for_finding_NN.append('tvpl1')
feature_list_for_finding_NN.append('tvpl2')
feature_list_for_finding_NN.append('tvpl5')
feature_list_for_finding_NN.append('tvpl_ep1')
feature_list_for_finding_NN.append('tvpl_ep2')
feature_list_for_finding_NN.append('tvpl_ep5')
feature_list_for_finding_NN.append('trade_vol')
feature_list_for_finding_NN.append('trade.tau')
feature_list_for_finding_NN.append('return')

feature_list_for_finding_NN.append('volume_power')


In [88]:
main_feature_list = list(combined_result_df.columns)
feature_list_for_finding_NN.append(target_var)


# feature_list_for_corr = list(combined_result_df.columns)

# remove_varlist = [
#                   'time_id'
#                   ]

# for i in range(len(remove_varlist)):
#     # print(remove_varlist[i])
#     feature_list_for_corr.remove(remove_varlist[i])


gc.collect()

23

In [89]:
data = combined_result_df
correlation_matrix = data[feature_list_for_finding_NN].corr(method=lambda x, y: kendalltau(x, y).correlation)
feature_list_for_finding_NN.remove(target_var)

correlation_matrix_series = correlation_matrix[target_var].copy() # .sort_values(ascending=False)
correlation_matrix_series.sort_values(ascending=False, inplace=True)

gc.collect()

23

In [90]:
correlation_matrix_series

dv5_realized_volatility_mean0    1.000000
bidask_spread_1                  0.260661
realized_volatility_mean0        0.257185
bidask_spread_0                  0.234541
tvpl_ep1                         0.178763
tvpl_ep2                         0.172980
tvpl5                            0.161895
tvpl2                            0.160957
tvpl_ep5                         0.156592
tvpl1                            0.148675
high_low_gap                     0.143455
BB_width_w10                     0.120152
BB_width_w20                     0.081748
highest_return                   0.072720
BB_width_w40                     0.045355
trade_vol                        0.043915
return                           0.041393
num_trades                       0.037317
volume_power                     0.034003
trade.tau                       -0.037317
lowest_return                   -0.088506
liq_last_1                      -0.143123
liq_last_2                      -0.163738
liq_last_5                      -0

In [91]:
combined_result_df_mfl = combined_result_df

In [92]:
# combined_result_df_mfl.reset_index(drop=True, inplace=True)

In [93]:
combined_result_df_mfl.shape

(75030, 95)

In [94]:
import re
from joblib import Parallel, delayed
from numba import jit

# Numba를 사용하여 최적화된 Hausdorff 거리 계산 함수
@jit(nopython=True)
def compute_hausdorff_modified_numba(x, y):
    min_distances = np.abs(np.subtract(x, y))
    return np.max(min_distances)

# 주어진 시계열 대상과 다른 모든 시계열 간의 거리를 계산하는 함수
def compute_distances(target_series, series_list):
    return [compute_hausdorff_modified_numba(target_series, s) for s in series_list]

# 병렬 처리를 사용하여 특정 시계열과 가장 유사한 시계열의 인덱스를 찾는 함수
def parallel_similarity(df, idx, num_similar, window_size ):
    if idx < window_size :
        return np.array([0] * num_similar)
    
    target_series = np.array(df.iloc[idx])
    
    other_series = []
    
    for series in df.iloc[idx-window_size:idx] :
        other_series.append(np.array(series))
            
    distances = compute_distances(target_series, other_series)
    similar_indices = list(np.argsort(distances)[:num_similar])
    
    similar_indices = [(idx - window_size + x) for x in similar_indices]
    
    return similar_indices

# 병렬 처리를 사용하여 모든 시계열 간의 유사도를 계산하는 함수
def compute_similarity_parallel(df, num_similar=10, window_size = 10000):
    # 빈 2D 배열 생성
    results = np.array([]).reshape(0, num_similar)  # 2D 배열, 0행 2열
    
    for idx in range(len(df)):
        # if (idx + 1) % (len(df) // 10) == 0:
        #     print(f"Processed {idx + 1} rows ({((idx + 1) / len(df)) * 100:.1f}%)")
        result = parallel_similarity(df, idx, num_similar, window_size)
        results = np.append(results, [result], axis=0)
        
    return results

### BUILD NEIGHBORS

In [57]:
N_NEIGHBORS_MAX = 17        
WINDOW_SIZE = 20000

class Neighbors:
    def __init__(self, 
                 name: str, 
                 pivot: pd.DataFrame, 
                 p: float, 
                 metric: str = 'minkowski', 
                 metric_params: object = None, 
                 exclude_self: bool = True,
                 haus_metric = False,
                 ):
        self.name = name
        self.exclude_self = exclude_self
        self.p = p
        self.metric = metric
        self.neighbors = np.empty((0, N_NEIGHBORS_MAX), dtype=int)  # 빈 2D 배열로 초기화

        nn = NearestNeighbors(
            n_neighbors=N_NEIGHBORS_MAX, 
            p=p, 
            metric=metric, 
            metric_params=metric_params
        )
        
        # nn.fit(pivot)
        # _, self.neighbors = nn.kneighbors(pivot, return_distance=True)

        # 이웃을 찾을 이전 window 벙뮈
        window_size = WINDOW_SIZE

        if haus_metric == True : 
            # print("Checkpoint-haus_metric-BEGIN")

            self.neighbors = compute_similarity_parallel(listed_time_series_df, num_similar=N_NEIGHBORS_MAX, window_size = WINDOW_SIZE)
            self.neighbors = self.neighbors.astype(int)
            # print("Checkpoint-haus_metric-END")

        else:
            col_names = pivot.columns
            index_name = pivot.index.name
            
            for t in range(len(pivot)) :
                if t % 1000 == 0:
                    print("name: {}, iteration: {}".format(self.name, t))
                # window size 까지의 데이터는 random NN 설정
                # 1 ~ window 범위의 데이터는 추후 버려야 함
                if t < window_size :
                    update_array = np.random.permutation(np.arange(1, N_NEIGHBORS_MAX+1))
                    self.neighbors = np.append(self.neighbors, [update_array], axis = 0)
                    
                else :
                    # print("Checkpoint#1")

                    # pvdf = pd.DataFrame(pivot.iloc[t-window_size:t])
                    pvdf = pivot.iloc[t-window_size:t].values
                    # print("Checkpoint#1-1-0, pvdf.head(1):", pvdf.head(1))

                    # print("Checkpoint#1-1-1, list(col_names):", list(col_names))
                    # print("Checkpoint#1-1-2, type([list(col_names)]):", type([list(col_names)]))

                    # # col_names = list(col_names)
                    # # pvdf.columns = col_names
                    # print("Checkpoint#1-2")
                    # print("Checkpoint#1-2-1, //after// pvdf.columns:", pvdf.columns)

                    # pvdf.columns = list(col_names)
                    # pvdf = pvdf.rename_axis(index_name)
                    # print("Checkpoint#1-3")

                    nn.fit(pvdf)
                  
                    # print("Checkpoint#2")
                    update_array = nn.kneighbors(pivot.iloc[t].values.reshape(1,-1), n_neighbors=N_NEIGHBORS_MAX , return_distance=False)
                                      
                    # print("Checkpoint#3, update_array:", update_array)

                    update_array = update_array.reshape(-1) + (t-window_size)
                    # print("Checkpoint#4")

#                     print("self.neighbors.shape", self.neighbors.shape)
#                     print("update_array.shape", update_array.shape)

                    # self.neighbors = np.append(self.neighbors, update_array, axis = 0)
                    self.neighbors = np.vstack((self.neighbors, update_array))
#                     print("NEWLY UPDATED self.neighbors.shape", self.neighbors.shape)

                    # print("Checkpoint#5")

                    # if t // 10000 == 0 :
                    #    print(t,self.neighbors)
                    gc.collect()


        self.columns = self.index = self.feature_values = self.feature_col = None

    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str) -> None:
        raise NotImplementedError()

    def make_nn_feature(self, n=5, agg=np.mean) -> pd.DataFrame:
        assert self.feature_values is not None, "should call rearrange_feature_values beforehand"

        start = 0 if self.exclude_self else 0 # 이미 window 내에 자기자신이 없으므로 start= 0 이어도 된다.

        pivot_aggs = pd.DataFrame(
            agg(self.feature_values[start:n+start,:,0], axis=0), 
            columns=self.columns, 
            index=self.index[WINDOW_SIZE:]
        )

        dst = pivot_aggs.reset_index() # unstack().
        # print("dst.shape:", dst.shape)
        new_column_names = ['time_id', f'{self.feature_col}_nn{n}_{self.name}_{agg.__name__}'] # 3개를 예측했는데 2개만 들어왔다??
        dst.columns = new_column_names 
        return dst
    

class TimeIdNeighbors(Neighbors):
    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str, data_df: pd.DataFrame) -> None:
        # feature_pivot = df.pivot(index='time_id', values=feature_col)
        # feature_pivot = feature_pivot.fillna(feature_pivot.mean())

        # print('CHEKCPOINT#1')
        feature_df = data_df[['time_id', feature_col]]
        # print('CHEKCPOINT#2')

        # 첫 WINDOW_SIZE 만큼은 랜덤하게 부여된 이웃이므로 제거.
        # feature_df = feature_df.drop(range(WINDOW_SIZE))

        feature_df.set_index('time_id', inplace=True)
        # feature_df = feature_df.fillna(feature_df.mean())

        feature_values = np.zeros((N_NEIGHBORS_MAX, df.shape[0], 1))
        temp_neighbors = self.neighbors[WINDOW_SIZE:,:]
 
        # print("feature_values", feature_values.shape)
        # print("feature_df", feature_df.shape)
        # print("self.neighbors.shape", self.neighbors.shape)
        # print("temp_neighbors", temp_neighbors.shape)

        for i in range(N_NEIGHBORS_MAX):
            # feature_values[i, :, 0] += feature_df.values[self.neighbors[:, i], 0]
            feature_values[i, :, 0] += feature_df.values[temp_neighbors[:, i], 0]

        self.columns = list(feature_df.columns)
        self.index = list(feature_df.index)
        self.feature_values = feature_values
        self.feature_col = feature_col

    def __repr__(self) -> str:
        return f"time-id NN (name={self.name}, metric={self.metric}, p={self.p})"


### PROGRESS CHECK FUNCTION

In [58]:
@contextmanager
def timer(name: str):
    s = time.time()
    yield
    elapsed = time.time() - s
    print(f'[{name}] {elapsed: .3f}초')

def print_trace(name: str = ''):
    print(f'{name or "익명"}에서 에러가 발생했습니다.')
    print(traceback.format_exc())


### GET NN CLASS. Output: {}_sum_plus_nn_features.csv

In [59]:
from sklearn.preprocessing import StandardScaler
from itertools import combinations

# StandardScaler 객체 생성
scaler = StandardScaler()

USE_ONE_FEATURE_C = False
USE_ONE_FEATURE_M_1 = True
USE_ONE_FEATURE_M_2 = False

USE_TWO_FEATURES = True
USE_TWO_FEATURES_ALL_COMB = False
USE_SEVALRAL_FEATURES = True
USE_ALL_FEATURES = True

USE_HAUSDORFF_FEATURES = False

# Top 5 Related Feature
top_5_high_feat = list(correlation_matrix_series.keys())[1:6]
top_5_low_feat = list(correlation_matrix_series.keys())[-5:]

# Top 5 Absolute Related Feature
sorted_data = correlation_matrix_series.abs().sort_values(ascending=False)
top_5_high_abs_feat = list(sorted_data.head(6).keys())[1:]
top_5_low_abs_feat = list(sorted_data.tail(5).keys())

# time_id_neighbors List 
time_id_neighbors: List[Neighbors] = []

with timer('knn fit'):
    df_pv = combined_result_df_mfl.copy()
    # df_pv = df_pv.drop(['window_start', 'window_end','volume_power'], axis=1)
    
    # Standard All Feature
    # df_pv[feature_list_for_finding_NN] = scaler.fit_transform(df_pv[feature_list_for_finding_NN])

    feature_list = list(df_pv.columns)
    feature_list.remove('time_id') # Can't be standardized
    # feature_list.remove('only_prices_30s_for_NN')
    # feature_list.remove('prices_30s_for_NN_onlyprices') # Can't be standardized
    # feature_list.remove('time_id')
    df_pv[feature_list] = scaler.fit_transform(df_pv[feature_list])
    # combined_result_df_mfl_scaled.head(3)



    #### USE ONLY ONE FACTOR ####

    # ## Canberra Distance
    if USE_ONE_FEATURE_C :
        print("ONE FACTOR: Canberra Distance")
        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(
                    feat + '_c', 
                    df_nn, 
                    p=2, 
                    metric='canberra', 
                    exclude_self=True
                )
            )
            
    ## Manhattan Distance
    
    if USE_ONE_FEATURE_M_1:
        print("ONE FACTOR: Manhattan Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p1', df_nn, p=1, exclude_self=True)
            )

    # ## Euclidean Distance
    if USE_ONE_FEATURE_M_2:
        print("ONE FACTOR: Euclidean Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p2', df_nn, p=2, exclude_self=True)
            )


    # #### TWO FACTOR ####

    if USE_TWO_FEATURES:
        feature_list = ['time_id','realized_volatility_mean0','bidask_spread_0'] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        df_nn = df_nn.fillna(df_nn.mean())

        # ## Canberra

        # time_id_neighbors.append(
        #         TimeIdNeighbors(
        #             'two_c',  # before correction: feat + 'two_c', 
        #             df_nn, 
        #             p=2, 
        #             metric='canberra', 
        #             exclude_self=True
        #         )
        #     )
        ## Euclidean Distance
        time_id_neighbors.append(
            TimeIdNeighbors(
                'two_m', 
                df_nn, 
                p=2, 
                exclude_self=True
            )
        )


    if USE_TWO_FEATURES_ALL_COMB:
        print("TWO FACTORS: all possible combinations")

        combinations_list = list(combinations(feature_list_for_finding_NN, 2))

        for feat in combinations_list :
            gc.collect()
            # feature_list_for_finding_NN
            # combinations_list = list(combinations(feature_list_for_finding_NN, 2))

            feature_list = ['time_id',feat[0],feat[1]] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
            df_nn = df_pv[feature_list]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            ## Canberra

            # time_id_neighbors.append(
            #         TimeIdNeighbors(
            #             'two_c',  # before correction: feat + 'two_c', 
            #             df_nn, 
            #             p=2, 
            #             metric='canberra', 
            #             exclude_self=True
            #         )
            #     )
            ## Euclidean Distance
            time_id_neighbors.append(
                TimeIdNeighbors(
                    'two_comb_{}_{}_m'.format(feat[0],feat[1]), 
                    df_nn, 
                    p=2, 
                    exclude_self=True
                )
            )



    #### USE SEVALRAL FACTOR ####

    if USE_SEVALRAL_FEATURES:
        print("FIVE FACTORS")

        ## High Related Feature 
        feature_list = ['time_id']
        feature_list += top_5_high_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        ### Euclidean Distance
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())        

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## High Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_high_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())
        
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )


    #### USE ALL FACTOR ####

    if USE_ALL_FEATURES:
        print("ALL FACTORS")

        df_nn = df_pv.copy()
        # df_nn = df_nn.drop(['dv1_realized_volatility'], axis=1)
        df_nn.set_index('time_id', inplace=True)

        # Standard All Feature
        # df_nn[feature_list_for_finding_NN] = scaler.fit_transform(df_nn[feature_list_for_finding_NN])

        df_nn = df_nn[feature_list_for_finding_NN]
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'all_nn_m_p1', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        # time_id_neighbors.append(
        #     TimeIdNeighbors(
        #         'all_nn_m_p2', 
        #         df_nn, 
        #         p=2, 
        #         exclude_self=True
        #     )
        # )

    #### HAUSDORFF

    if USE_HAUSDORFF_FEATURES:
        print("HAUSDORFF")

        time_id_neighbors.append(
                TimeIdNeighbors('hausdorff', None, p=0, exclude_self=True, haus_metric = True)
        )


ONE FACTOR: Manhattan Distance
name: realized_volatility_mean0_m_p1, iteration: 0
name: realized_volatility_mean0_m_p1, iteration: 1000
name: realized_volatility_mean0_m_p1, iteration: 2000
name: realized_volatility_mean0_m_p1, iteration: 3000
name: realized_volatility_mean0_m_p1, iteration: 4000
name: realized_volatility_mean0_m_p1, iteration: 5000
name: realized_volatility_mean0_m_p1, iteration: 6000
name: realized_volatility_mean0_m_p1, iteration: 7000
name: realized_volatility_mean0_m_p1, iteration: 8000
name: realized_volatility_mean0_m_p1, iteration: 9000
name: realized_volatility_mean0_m_p1, iteration: 10000
name: realized_volatility_mean0_m_p1, iteration: 11000
name: realized_volatility_mean0_m_p1, iteration: 12000
name: realized_volatility_mean0_m_p1, iteration: 13000
name: realized_volatility_mean0_m_p1, iteration: 14000
name: realized_volatility_mean0_m_p1, iteration: 15000
name: realized_volatility_mean0_m_p1, iteration: 16000
name: realized_volatility_mean0_m_p1, iteration

In [ ]:
# time_id_neighbors 변수를 pickle 파일에 저장

import pickle

file_name = "time_id_neighbors.pkl"
with open(file_name, 'wb') as file:
    pickle.dump(time_id_neighbors, file)


In [ ]:
# pickle 파일에서 변수를 불러오기

import pickle

file_name = "time_id_neighbors.pkl"

with open(file_name, 'rb') as file:
    loaded_time_id_neighbors = pickle.load(file)


#### Aggregate Features With NN

In [60]:
def make_nearest_neighbor_feature(df: pd.DataFrame, data_df: pd.DataFrame) -> pd.DataFrame:
    df2 = df.copy()
    print(df2.shape)

    ### time_id를 기준으로 얻어진 neighbor를 대상으로 feature 만들기
    feature_cols = {
        # 'realized_volatility': [np.mean], #, np.min, np.max, np.std
        'realized_volatility_mean0': [np.mean, np.median], # , np.median
        # 'realized_volatility_30s': [np.mean, np.median],

        # 'dv1_realized_volatility': [np.mean],
        'dv2_lowest_return': [np.mean, np.median],
        'dv3_highest_return': [np.mean, np.median],
        # 'dv4_realized_volatility_30s': [np.mean, np.median],
        'dv5_realized_volatility_mean0': [np.mean, np.median],

        'num_trades': [np.mean, np.median],
        'lowest_return': [np.mean, np.median], # , np.mean, np.min
        'highest_return': [np.mean, np.median], # , np.mean, np.min
        'high_low_gap': [np.mean, np.median],
        'trade_vol': [np.mean, np.median],
        # 'volume_power': [np.mean],
        'BB_width_w10': [np.mean, np.median],
        'BB_width_w20': [np.mean, np.median],
        'BB_width_w40': [np.mean, np.median],

        'liq_last_1': [np.mean, np.median],
        'liq_last_2': [np.mean, np.median],
        'liq_last_5': [np.mean, np.median],
        'ep_liq_1': [np.mean, np.median],
        'ep_liq_2': [np.mean, np.median],
        'ep_liq_5': [np.mean, np.median],
        'bidask_spread_0': [np.mean, np.median],
        'bidask_spread_1': [np.mean, np.median],

        'tvpl1': [np.mean, np.median],
        'tvpl2': [np.mean, np.median],
        'tvpl5': [np.mean, np.median],
        'tvpl_ep1': [np.mean, np.median],
        'tvpl_ep2': [np.mean, np.median],
        'tvpl_ep5': [np.mean, np.median],
        'trade.tau': [np.mean, np.median],
        'return': [np.mean, np.median],

    }

    time_id_neigbor_sizes = [1, 2, 4, 8, 16] # 16, 32, 48, 64 메모리 부족으로 계속 오류가 나는 것 같아 이웃 계산 숫자를 줄임.

    ndf: Optional[pd.DataFrame] = None
    
    # 새로운 feature를 기존 df에 추가하는 함수
    def _add_ndf(ndf: Optional[pd.DataFrame], dst: pd.DataFrame) -> pd.DataFrame:
        if ndf is None:
            return dst
        else:
            ndf[dst.columns[-1]] = dst[dst.columns[-1]].astype(np.float32)
            #columns_to_convert = [dst.columns[-1]]  # 열 변환 대상을 선택하거나 여러 열을 지정할 수 있음
            #converted_columns = dst[columns_to_convert].astype(np.float32)
            #ndf = pd.concat([ndf, converted_columns], axis=1)

            return ndf

    # neighbor time_id
    for feature_col in feature_cols.keys():
        gc.collect()
        try: 
            for nn in time_id_neighbors:
                nn.rearrange_feature_values(df2, feature_col, data_df)


            time_id_ns = time_id_neigbor_sizes

            for agg in feature_cols[feature_col]:
                for n in time_id_ns:
                    try:
                        for nn in time_id_neighbors:
                            gc.collect()
                            dst = nn.make_nn_feature(n, agg)
                            ndf = _add_ndf(ndf, dst)
                    except Exception:
                        WHERE_ERROR = feature_col
                        print_trace('time-id nn')
                        pass
        except Exception:
            print_trace('time-id nn')

    if ndf is not None:
        df2 = pd.merge(df2, ndf, on=['time_id'], how='left')
    
    print(df2.shape)
    gc.collect()
    return df2

In [61]:
# print(type(time_id_neighbors))
print(time_id_neighbors[0].neighbors[:,:10])
print(np.max(time_id_neighbors[0].neighbors[:,:10]))


[[    1    14     9 ...     5     4     8]
 [   14     6     2 ...    13     4     9]
 [    7     3     9 ...    15    10    14]
 ...
 [66768 60539 59354 ... 53150 54048 51673]
 [59150 62372 65713 ... 61062 66436 65710]
 [54265 54270 61919 ... 57795 54709 61154]]
68288


In [62]:
pd.set_option('display.max_columns', None)

combined_result_df.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000224         371      -0.000594        0.000548   
1                   0.000212         457      -0.000869        0.000548   
2                   0.000200         472      -0.000731        0.000685   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.001143  17.601431  2022-12-23 12:42:00  28224.662109  30594.787109   
1      0.001417  21.580793  2022-12-23 12:43:00  28298.410156  30489.341797   
2      0.001417  23.135344  2022-12-23 12:44:00  28059.335938  29803.458984   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  25469.808594                       0.000133          -0.000229   
1  24887.300781                       0.000129          -0.000091   
2  24819.347656                       0.000131          -0.000046   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.001005                       0.000221              78   
1            0.001279                       0.000256              83   
2            0.001325                       0.000212              87   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000229            0.000548          0.000777       3.783830   
1          -0.000594            0.000274          0.000868       2.940242   
2          -0.000457            0.000320          0.000777       3.022768   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000221             159          -0.000320   
1                       0.000254             169          -0.000869   
2                       0.000253             161          -0.000731   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000548          0.000868       6.653337   
1            0.000274          0.001143       6.528900   
2            0.000320          0.001051       5.719865   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000249             246          -0.000594   
1                       0.000247             261          -0.000869   
2                       0.000227             274          -0.000731   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000548          0.001143       9.991838    0.000270   
1            0.000274          0.001143      10.267628    0.000121   
2            0.000366          0.001097       9.853143    0.000090   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.001822    0.002066     0.002159     0.002579  0.000152  0.000245   
1    0.001779    0.001914     0.002146     0.002466  0.000160  0.000270   
2    0.003336    0.003445     0.003838     0.004130  0.000226  0.000388   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.000470   0.000670   0.001060         6.580247         9.123457   
1  0.000498   0.000715   0.001088         4.060606         9.757576   
2  0.000609   0.000841   0.001190         5.961538        10.894231   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.000072        0.000269        0.000395         0.000661   
1        0.000386        0.000618        0.000731         0.000977   
2        0.000139        0.000266        0.000417         0.000645   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.000915      0.000115      0.000181      0.000446       0.000643   
1         0.001298      0.000081      0.000148      0.000407       0.000661   
2         0.000893      0.000148      0.000228      0.000432       0.000702   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.001069             4.272727            14.227273        0.000058   
1       0.001025             7.020000            15.580000        0.000153   
2       

In [63]:
combined_result_df_mfl.tail(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
68317                   0.000126         411       0.000000        0.001802   
68318                   0.000153         456      -0.000164        0.001638   
68319                   0.000161         460       0.000000        0.001802   

       high_low_gap  trade_vol              time_id  BB_width_w20  \
68317      0.001802  16.059008  2023-02-25 23:57:00  45523.390625   
68318      0.001802  19.924879  2023-02-25 23:58:00  45512.289062   
68319      0.001802  20.245977  2023-02-25 23:59:00  37592.832031   

       BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
68317  52926.558594  41270.921875                       0.000305   
68318  52806.757812  39420.242188                       0.000300   
68319  52653.781250  33899.195312                       0.000286   

       dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
68317          -0.000590            0.001342                       0.000066   
68318          -0.000066            0.001866                       0.000033   
68319          -0.000066            0.001866                       0.000087   

       num_trades_150  lowest_return_150  highest_return_150  \
68317              38           0.000000            0.000197   
68318              61          -0.000164            0.000066   
68319              93           0.000000            0.000590   

       high_low_gap_150  trade_vol_150  realized_volatility_mean0_300  \
68317          0.000197       1.278633                       0.000082   
68318          0.000229       2.693161                       0.000076   
68319          0.000590       2.714263                       0.000075   

       num_trades_300  lowest_return_300  highest_return_300  \
68317             138           0.000000            0.000590   
68318             162          -0.000164            0.000524   
68319             188           0.000000            0.000983   

       high_low_gap_300  trade_vol_300  realized_volatility_mean0_450  \
68317          0.000590       4.511645                       0.000090   
68318          0.000688       5.872967                       0.000129   
68319          0.000983       6.236995                       0.000129   

       num_trades_450  lowest_return_450  highest_return_450  \
68317             279           0.000000            0.001540   
68318             331          -0.000164            0.001638   
68319             345           0.000000            0.001802   

       high_low_gap_450  trade_vol_450  liq_last_1  liq_last_2  liq_last_5  \
68317          0.001540      12.494351    0.000147    0.000193    0.000470   
68318          0.001802      13.827040    0.000348    0.000379    0.000456   
68319          0.001802      13.619727    0.000006    0.000129    0.000894   

       liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  ep_liq_5  ep_liq_10  \
68317     0.000695     0.000729  0.000127  0.000197  0.000323   0.000488   
68318     0.000682     0.000741  0.000121  0.000189  0.000318   0.000480   
68319     0.001108     0.001172  0.000122  0.000191  0.000332   0.000498   

       ep_liq_15  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
68317   0.000609         6.960976        13.507318        0.000192   
68318   0.000587        15.243093        25.696133        0.000615   
68319   0.000596        10.519737        21.282894        0.000222   

       liq_last_2_150  liq_last_5_150  liq_last_10_150  liq_last_15_150  \
68317        0.000402        0.000488         0.000597         0.000812   
68318        0.001216        0.001395         0.001517         0.001565   
68319        0.000229        0.000585         0.000706         0.000747   

       ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  ep_liq_15_150  \
68317      0.000179      0.000353      0.000469       0.000612       0.000838   
68318      0.000695      0.000942      0.001043       0.001160       0.001317   
68319      0.000393    

In [64]:
gc.collect()

# Cut the first WINDOW_SIZE rows
# input_df = combined_result_df_mfl.drop(index=range(WINDOW_SIZE))
input_df = combined_result_df_mfl.iloc[WINDOW_SIZE:]

with timer('make nearest neighbor feature'):
    df3 = make_nearest_neighbor_feature(input_df, combined_result_df_mfl)

gc.collect()

(48320, 91)


c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


(48320, 9051)
[make nearest neighbor feature]  747.998초


0

In [65]:
print(df3.shape)
df3.head(3)


(48320, 9051)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000242        1332      -0.004460        0.000000   
1                   0.000245        1225      -0.002322        0.002049   
2                   0.000252        1160      -0.001340        0.003031   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.004460  85.643402  2023-01-12 08:39:00  461979.03125   764972.0000   
1      0.004371  76.797997  2023-01-12 08:40:00  394194.65625   767098.0625   
2      0.004371  73.178680  2023-01-12 08:41:00  321457.93750   769054.3125   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  76129.710938                        0.00010          -0.000713   
1  71822.000000                        0.00010          -0.000089   
2  42392.871094                        0.00013           0.000000   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.001602                       0.000249             427   
1            0.002226                       0.000321             405   
2            0.002359                       0.000337             387   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.004460            0.000000          0.004460      26.014551   
1          -0.002322            0.001560          0.003882      26.465773   
2          -0.001340            0.003031          0.004371      28.808460   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000275             797          -0.004460   
1                       0.000287             715          -0.002322   
2                       0.000292             702          -0.001340   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000000          0.004460      53.933792   
1            0.002049          0.004371      48.617016   
2            0.003031          0.004371      48.894909   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000260            1091          -0.004460   
1                       0.000263             957          -0.002322   
2                       0.000267             943          -0.001340   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000000          0.004460      72.046455    0.000627   
1            0.002049          0.004371      61.811108    0.000026   
2            0.003031          0.004371      61.731346    0.001508   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.000740    0.000938     0.001313     0.001618  0.000330  0.000466   
1    0.000302    0.001418     0.001640     0.001678  0.000325  0.000470   
2    0.002247    0.003568     0.003861     0.003977  0.000303  0.000453   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.000783   0.001056   0.001220         4.851240        11.144629   
1  0.000807   0.001089   0.001258         8.189189        13.837838   
2  0.000817   0.001104   0.001274         5.232653         8.632653   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.002105        0.002913        0.003501         0.003652   
1        0.000045        0.000304        0.000504         0.000800   
2        0.000162        0.000163        0.000242         0.000360   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.003776      0.000335      0.000444      0.000701       0.000928   
1         0.000995      0.000267      0.000376      0.000601       0.000815   
2         0.000567      0.000236      0.000334      0.000562       0.000777   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.001057            10.118012            26.074533        0.000868   
1       0.000945             7.056338            13.183099        0.001319   
2       

In [66]:
df3.to_csv(working_directory + "output\\temp_1105_second_after_30000.csv", index=False)

In [68]:
import pandas as pd

# Create two sample dataframes
temp1 = pd.read_csv(working_directory +"output\\temp_1105_first_30000.csv")
temp2 = df3

print(temp1.shape)
print(temp2.shape)



(8411, 9051)
(48320, 9051)


In [69]:
# Concatenate them as new rows
result = pd.concat([temp1, temp2], ignore_index=True)

In [70]:
result.shape

(56731, 9051)

In [71]:
result.drop_duplicates(subset = 'time_id',keep='first', inplace=True)


In [72]:
result.shape

(55030, 9051)

In [160]:
temp1.tail(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
8879                   0.000203         365      -0.001948        0.000093   
8880                   0.000185         467      -0.002598        0.000139   
8881                   0.000175         549      -0.002830        0.000046   

      high_low_gap  trade_vol              time_id  BB_width_w20  \
8879      0.002040  19.208967  2023-01-04 13:57:00     41969.914   
8880      0.002737  25.359545  2023-01-04 13:58:00     50702.848   
8881      0.002876  29.646381  2023-01-04 13:59:00     62690.215   

      BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
8879     40503.370     47232.758                       0.000169   
8880     47045.970     59723.810                       0.000186   
8881     56604.703     73453.234                       0.000202   

      dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
8879          -0.001207            0.000603                       0.000059   
8880          -0.000790            0.001021                       0.000098   
8881          -0.000279            0.001532                       0.000305   

      num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
8879              75          -0.000278            0.000093          0.000371   
8880              87          -0.000232            0.000139          0.000371   
8881             103          -0.000927            0.000046          0.000973   

      trade_vol_150  realized_volatility_mean0_300  num_trades_300  \
8879       2.666636                       0.000253             160   
8880       3.258465                       0.000276             147   
8881       4.380208                       0.000286             147   

      lowest_return_300  highest_return_300  high_low_gap_300  trade_vol_300  \
8879          -0.001020            0.000093          0.001112       6.548009   
8880          -0.000973            0.000139          0.001112       6.101820   
8881          -0.000927            0.000046          0.000973       5.625350   

      realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
8879                       0.000239             221          -0.001020   
8880                       0.000223             256          -0.001159   
8881                       0.000228             285          -0.001716   

      highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
8879            0.000093          0.001112       8.841516    0.000390   
8880            0.000139          0.001298      12.222675    0.000322   
8881            0.000046          0.001762      13.674121    0.000006   

      liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
8879    0.000408    0.000661     0.001011     0.001197  0.000293  0.000428   
8880    0.000497    0.000602     0.000979     0.001133  0.000310  0.000449   
8881    0.001181    0.001599     0.001789     0.001959  0.000337  0.000488   

      ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
8879  0.000759   0.001049   0.001283         4.487395        10.563025   
8880  0.000766   0.001064   0.001271         1.511811         9.118111   
8881  0.000811   0.001099   0.001288         2.071429        12.335714   

      liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
8879        0.000131        0.000555        0.000749         0.001133   
8880        0.000057        0.000798        0.001016         0.001438   
8881        0.000009        0.000364        0.000813         0.001012   

      liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  \
8879         0.001613      0.000703      0.000841      0.001093   
8880         0.001831      0.000473      0.000590      0.000792   
8881         0.001163      0.000141      0.000259      0.000528   

      ep_liq_10_150  ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  \
8879       0.001449       0.001880             2.689655             6

In [161]:
temp2.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000054         333      -0.000139        0.000417   
1                   0.000060         364      -0.000650        0.000417   
2                   0.000069         408      -0.000882        0.000557   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.000557  20.134951  2023-01-04 21:11:00  27452.542969  42367.742188   
1      0.001067  20.520779  2023-01-04 21:12:00  23123.466797  42399.683594   
2      0.001439  20.930735  2023-01-04 21:13:00  27206.037109  42106.582031   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  12103.259766                       0.000196          -0.001160   
1  23232.162109                       0.000199          -0.000371   
2  35537.773438                       0.000198          -0.000046   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.000000                       0.000086              46   
1            0.000789                       0.000064              77   
2            0.001114                       0.000050              94   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000139            0.000139          0.000278       2.964197   
1          -0.000139            0.000139          0.000278       3.076633   
2           0.000000            0.000278          0.000278       3.414210   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000060             135          -0.000139   
1                       0.000050             141          -0.000139   
2                       0.000041             168           0.000000   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000139          0.000278       6.098859   
1            0.000139          0.000278       6.929142   
2            0.000418          0.000418       7.025306   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000052             217          -0.000139   
1                       0.000048             239          -0.000139   
2                       0.000047             284           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000278          0.000418      10.999846    0.001048   
1            0.000417          0.000557      11.801092    0.000303   
2            0.000557          0.000557      12.149213    0.004901   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.001121    0.001340     0.001443     0.002005  0.000964  0.001640   
1    0.000462    0.000920     0.001274     0.001467  0.000802  0.001418   
2    0.004906    0.005232     0.005565     0.005948  0.000691  0.001204   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.002220   0.002651   0.003337         2.300000         5.200000   
1  0.001975   0.002391   0.002976         3.486486         7.175676   
2  0.001669   0.002019   0.002451         3.649485         8.036082   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.000223        0.000361        0.000499         0.000767   
1        0.000345        0.000455        0.000616         0.000980   
2        0.007331        0.009770        0.009912         0.010154   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.001843      0.000626      0.000816      0.000964       0.001351   
1         0.001555      0.000440      0.000588      0.000726       0.001122   
2         0.010986      0.000867      0.001298      0.001567       0.001940   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.002238             3.000000             7.818182        0.006807   
1       0.001835             2.631579             7.947369        0.000152   
2       

In [73]:
# Cut the first 'window_size' (15,000 or something) rows. <= These rows do not have appropriate nearest neighbors.
# WINDOW_SIZE=20000
# df3 = df3.drop(index=range(WINDOW_SIZE))
vn = 2
coin = 'BTC'
result.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}_{}.csv".format(coin, target_var_3,vn), index=False)

## NN 추출끼리 비슷한가 아니면 다른가?

In [ ]:
def calculate_rank_correraltion(neighbors, top_n=10):
    if not neighbors:
        return
    neighbor_indices = pd.DataFrame()
    for n in neighbors:
        neighbor_indices[n.name] = n.neighbors[:,:top_n].flatten()
        display(neighbor_indices[n.name])
    sns.heatmap(neighbor_indices.corr('kendall'), annot=True)
    

In [ ]:
time_ids = np.array(sorted(df3['time_id'].unique()))
for neighbor in time_id_neighbors:
    print(neighbor)
    display(
        pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).iloc[1:6]
    )
    print(pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).shape)

In [ ]:
calculate_rank_correraltion(time_id_neighbors)

In [ ]:
# # TEMP code

# import gc
# import pandas as pd
# import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
# working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# # working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

# os.chdir(working_directory)
# gc.collect()

# # combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
# coin = 'BTC'
# target_var = 'dv5_realized_volatility_mean0'
# target_var_3 = target_var[:3]
# df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

# window_size=10000
# df3 = df3.drop(index=range(window_size))
# df3.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3), index=False)


### Checking the final outcome

In [ ]:
import gc
import pandas as pd
import os
os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
coin = 'BTC'
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

df3.head(3)
print("# of rows:", df3.shape[0])
print("# of columns:", df3.shape[1])

In [ ]:
df3.columns